In [1]:
import networkx as nx
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import json

In [2]:
data = pd.read_csv('data0.csv')
data["date"] = pd.to_datetime(data["date"]) 
date_begin=pd.to_datetime('2021-01-01')
date_end=pd.to_datetime('2022-12-31')
data=data[(data['date']>=date_begin)&(data['date']<=date_end)]

prediction=pd.read_csv('problem1_prediction.csv')
prediction['ds'] = pd.to_datetime(prediction['ds'])


date=pd.to_datetime('2023-01-31')
new_edge_value=1000
load_value=10000
res_value=100000
step=1

data.head()
# print(date+ pd.Timedelta(days=1))

place1 place2       date  num
0    DC3    DC5 2021-01-01    3
1    DC3   DC10 2021-01-01    4
2    DC3   DC14 2021-01-01    4
3    DC5    DC3 2021-01-01   41
4    DC5    DC9 2021-01-01    3

In [3]:
def cost_func(u,v,not_used,current_flow,max_flow):
    load_rate=current_flow/max_flow
    res_flow=max_flow-current_flow
    if u=='s' or v=='t':
        return 0
    if '-pre' in u or '-next' in v:
        return 0
    return np.ceil(not_used*new_edge_value +load_rate*load_value+res_value/(res_flow+1))

In [4]:
unique_routes = data[['place1', 'place2']].drop_duplicates()
edge_info=pd.DataFrame(columns=['max_flow','place1','place2','current_flow'])
for index, row in unique_routes.iterrows():
    place1,place2=row['place1'],row['place2']
    if 'DC5' in [place1,place2]:
        continue
    max_flow_1=data[(data['place1']==place1) & (data['place2']==place2)]['num'].max()
    max_flow_2=prediction[(prediction['place1']==place1) & (prediction['place2']==place2)]['yhat'].max()
    max_flow=max(max_flow_1,max_flow_2)
    current_flow=prediction[(prediction['ds']==date) & (prediction['place1']==place1) & (prediction['place2']==place2)]['yhat'].values[0]
    edge_info.loc[index]=[max_flow,place1,place2,current_flow]
edge_info=edge_info.reset_index()
edge_info.head() 

index max_flow place1 place2 current_flow
0      1     2011    DC3   DC10            0
1      2      242    DC3   DC14            1
2      8     1561    DC7    DC3            1
3     10     7759    DC7    DC9            0
4     11     6979    DC7   DC10         1263

In [5]:
unique_points=pd.concat([data['place1'],data['place2']],ignore_index=True).drop_duplicates()
point_info=pd.DataFrame(columns=['place','res','max_flow','in_flow','out_flow'])
for index, value in unique_points.iteritems():
    if value=='DC5':
        continue
    in_flow=prediction[(prediction['ds']==date)&(prediction['place2']==value)&(prediction['place1']!='DC5') ]['yhat'].sum( )
    out_flow=prediction[(prediction['ds']==date)&(prediction['place1']==value)&(prediction['place2']!='DC5')]['yhat'].sum( )
    res=out_flow-in_flow
    
    max_in_sum_1_temp=data[(data['place2']==value)].groupby('date').sum()
    max_in_sum_1=max_in_sum_1_temp['num'].max()
    max_in_sum_2_temp=prediction[(prediction['place2']==value)][['yhat','ds']].groupby('ds').sum()
    max_in_sum_2=max_in_sum_2_temp['yhat'].max()
    if np.isnan(max_in_sum_1):
        max_in_sum_1=0
    if np.isnan(max_in_sum_2):
        max_in_sum_2=0
    max_in_sum=max(max_in_sum_1,max_in_sum_2)
    
    max_out_sum_1_temp=data[(data['place1']==value)].groupby('date').sum()
    max_out_sum_1=max_out_sum_1_temp['num'].max()
    max_out_sum_2_temp=prediction[(prediction['place1']==value)].groupby('ds').sum()
    max_out_sum_2=max_out_sum_2_temp['yhat'].max()
    if np.isnan(max_out_sum_1):
        max_out_sum_1=0
    if np.isnan(max_out_sum_2):
        max_out_sum_2=0
    max_out_sum=max(max_out_sum_1,max_out_sum_2)
    
    point_info.loc[index]=[value,res,max(max_in_sum,max_out_sum),in_flow,out_flow]
point_info=point_info.reset_index()
point_info.head()

index place      res max_flow in_flow out_flow
0      0   DC3     -164   560123     170        6
1      8   DC7     4769    14128       0     4769
2     13   DC9     -130  1118681     142       12
3     21  DC10  -209030  1275839  354255   145225
4     28  DC12      -38   118782      45        7

In [6]:
# 创建有向图
G = nx.DiGraph()

# 添加节点
G.add_node('s')  # 源节点
G.add_node('t')  # 汇节点 

G.nodes['s']['demand']=-step
G.nodes['t']['demand']=step
for index, row in point_info.iterrows():
    point,max_flow,res,in_flow,out_flow=row['place'],row['max_flow'],row['res'],row['in_flow'],row['out_flow']
    G.add_node(point)
    G.add_node(point+'-pre')
    G.add_node(point+'-next')
    
    G.add_edge(point+'-pre', point, capacity=max(max_flow-in_flow,0), weight=0,flow=0,origin_capacity=max(0,max_flow-in_flow))
    G.add_edge(point, point+'-next', capacity=max(max_flow-out_flow,0), weight=0,flow=0,origin_capacity=max(0,max_flow-in_flow))
# print(G.nodes())
# 添加边
for index, row in edge_info.iterrows():
    u,v,max_flow,current_flow=row['place1'],row['place2'],row['max_flow'],row['current_flow']
    cost=cost_func(u,v,True,current_flow,max_flow)
    G.add_edge(u+'-next', v+'-pre', capacity=max(0,max_flow-current_flow), weight=cost,flow=current_flow,origin_capacity=max_flow)

for index, row in point_info.iterrows():
    place,res,max_flow=row['place'],row['res'],row['max_flow']
    if res>0:
        G.add_edge('s', place+'-pre', capacity=1e8, weight=0,flow=0,origin_capacity=1e8)
    else:
        G.add_edge(place+'-next', 't', capacity=1e8, weight=0,flow=0,origin_capacity=1e8)


flow_to_DC5=prediction[(prediction['ds']==date) & (prediction['place2']=='DC5')]['yhat'].sum()
flowDict=nx.max_flow_min_cost(G, 's', 't', capacity='capacity', weight='weight')
max_flow=sum(flowDict[node1][node2] for node1 in flowDict for node2 in flowDict[node1])
print(flow_to_DC5,max_flow)
min_cost_list=[]
flow_dict_list=[]

add_num,i=1,0
while i<flow_to_DC5:
    print(f'{i}/{flow_to_DC5}')
    i+=add_num
    if add_num<step:
        add_num+=1
    flowDict = nx.min_cost_flow(G, demand="demand", capacity='capacity', weight='weight')
    min_cost=nx.cost_of_flow(G,flowDict)
    min_cost_list.append(min_cost)
    flow_dict_list.append(flowDict)
    # print(min_cost)
    for u, v in G.edges():
        if flowDict[u][v]!=0:
            # print(u,v,flowDict[u][v])
            G[u][v]['capacity']-=flowDict[u][v]
            G[u][v]['flow']  += flowDict[u][v]
            G[u][v]['weight']=cost_func(u,v,False,G[u][v]['flow'],G[u][v]['origin_capacity'])
            # print(u,v,G[u][v]['weight'])
    


215749 17060330
0/215749
1/215749
2/215749
3/215749
4/215749
5/215749
6/215749
7/215749
8/215749
9/215749
10/215749
11/215749
12/215749
13/215749
14/215749
15/215749
16/215749
17/215749
18/215749
19/215749
20/215749
21/215749
22/215749
23/215749
24/215749
25/215749
26/215749
27/215749
28/215749
29/215749
30/215749
31/215749
32/215749
33/215749
34/215749
35/215749
36/215749
37/215749
38/215749
39/215749
40/215749
41/215749
42/215749
43/215749
44/215749
45/215749
46/215749
47/215749
48/215749
49/215749
50/215749
51/215749
52/215749
53/215749
54/215749
55/215749
56/215749
57/215749
58/215749
59/215749
60/215749
61/215749
62/215749
63/215749
64/215749
65/215749
66/215749
67/215749
68/215749
69/215749
70/215749
71/215749
72/215749
73/215749
74/215749
75/215749
76/215749
77/215749
78/215749
79/215749
80/215749
81/215749
82/215749
83/215749
84/215749
85/215749
86/215749
87/215749
88/215749
89/215749
90/215749
91/215749
92/215749
93/215749
94/215749
95/215749
96/215749
97/215749
98/215749
99/2

In [7]:
result_dict = {}
for d in flow_dict_list:
    for k1, v1 in d.items():
        if k1 not in result_dict:
            result_dict[k1] = {}
        for k2, v2 in v1.items():
            result_dict[k1][k2] = result_dict[k1].get(k2, 0) + v2
result_dict_new={}          
for k1,v1 in result_dict.items():
    for k2,v2 in v1.items():
        if v2!=0:
            k1=k1.replace('-pre','').replace('-next','')
            k2=k2.replace('-pre','').replace('-next','')
            if k1==k2:
                continue
            if k1 not in result_dict_new:
                result_dict_new[k1] = {}
            result_dict_new[k1][k2] = v2
result_dict=result_dict_new
for k1,v1 in result_dict.items():
    for k2,v2 in v1.items():
        if not(k1=='s' or k2=='t'):
            max_flow=edge_info[(edge_info['place1']==k1) & (edge_info['place2']==k2)]['max_flow'].values[0]
            origin_flow=edge_info[(edge_info['place1']==k1) & (edge_info['place2']==k2)]['current_flow'].values[0]
            result_dict[k1][k2] = [v2,(v2+origin_flow)/max_flow,max_flow,origin_flow]
        else:
            result_dict[k1][k2] = [v2,0,0,0]


df = pd.DataFrame([(k1, k2, v2[0],v2[1],v2[2],v2[3],date) for k1,v1 in result_dict.items() for k2,v2 in v1.items()], columns=['place1', 'place2', 'flow','load_rate','max_flow','origin_flow','date'])
df.to_csv('problem2_31.csv', index=True)  
result_dict
            

{'s': {'DC15': [8041, 0, 0, 0],
  'DC17': [11279, 0, 0, 0],
  'DC19': [11285, 0, 0, 0],
  'DC20': [7039, 0, 0, 0],
  'DC22': [2987, 0, 0, 0],
  'DC23': [11549, 0, 0, 0],
  'DC25': [23728, 0, 0, 0],
  'DC30': [3070, 0, 0, 0],
  'DC36': [6101, 0, 0, 0],
  'DC38': [10075, 0, 0, 0],
  'DC41': [2953, 0, 0, 0],
  'DC44': [12485, 0, 0, 0],
  'DC46': [3739, 0, 0, 0],
  'DC47': [34741, 0, 0, 0],
  'DC48': [6312, 0, 0, 0],
  'DC49': [2705, 0, 0, 0],
  'DC51': [33835, 0, 0, 0],
  'DC58': [10972, 0, 0, 0],
  'DC18': [7135, 0, 0, 0],
  'DC27': [5718, 0, 0, 0]},
 'DC3': {'t': [32406, 0, 0, 0]},
 'DC9': {'t': [85373, 0, 0, 0]},
 'DC10': {'t': [13788, 0, 0, 0]},
 'DC12': {'t': [12610, 0, 0, 0]},
 'DC14': {'t': [6269, 0, 0, 0]},
 'DC15': {'DC9': [8041, 0.10026934683392773, 80194, 0]},
 'DC17': {'DC3': [5010, 0.10018397056470965, 50008, 0],
  'DC14': [6269, 0.10022702564430518, 62548, 0]},
 'DC19': {'DC3': [4827, 0.10017213845739055, 48217, 3],
  'DC12': [5481, 0.10019904676685963, 54761, 6],
  'DC35': 

In [8]:
# G_result = nx.DiGraph()

# # 添加边和边的属性
# for u in result_dict:
#     for v, flow in result_dict[u].items():
#         if result_dict[u][v]==0:
#             continue
#         if u=='s' or v=='t':
#             continue
#         G_result.add_node(u)
#         G_result.add_node(v)
#         G_result.add_edge(u, v, flow=flow, capacity=G[u][v]['capacity'], weight=G[u][v]['weight'])

# # 可视化
# pos = nx.spring_layout(G_result,k=10)
# plt.figure(figsize=(8, 8))
# nx.draw_networkx_nodes(G_result, pos, node_size=50)
# nx.draw_networkx_labels(G_result, pos, font_size=8)
# edge_labels = {(u, v): f"{d['flow']}/{d['capacity']}" for u, v, d in G_result.edges(data=True)}
# nx.draw_networkx_edges(G_result, pos, alpha=0.8)
# nx.draw_networkx_edge_labels(G_result, pos, edge_labels=edge_labels, font_size=6)
# plt.axis('off')
# plt.show()